1. Install important libraries

In [3]:
!pip install lxml
!pip install folium

import pandas as pd
import numpy as np
import types
from botocore.client import Config
import ibm_boto3
import types
import pandas as pd
from botocore.client import Config
import ibm_boto3
import folium 
import requests
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMean
import json 

print('Libraries imported.')

2. Get data from the different neighborhoods of freiburg


In [12]:
# The code was removed by Watson Studio for sharing.

Neighborhood   Latitude  Longitude
0       Altstadt  47.994722   7.850000
1        Neuburg  48.000000   7.853611
2        Herdern  48.008889   7.862778
3      Zähringen  48.023889   7.863333
4          Brühl  48.027222   7.850833
5       Hochdorf  48.050000   7.801944
6        Waldsee  47.986389   7.884444
7   Littenweiler  47.979444   7.896667
8          Ebnet  47.986389   7.904722
9         Kappel  47.968056   7.909167
10        Oberau  47.990556   7.865556
11        Wiehre  47.984889   7.851944
12    Günterstal  47.965417   7.857222
13    Stühlinger  48.001111   7.838056
14      Mooswald  48.013611   7.825833
15  Betzenhausen  48.008333   7.816667
16    Landwasser  48.023889   7.808889
17         Lehen  48.017500   7.801944
18  Waltershofen  48.023889   7.721389
19     Mundenhof  48.016667   7.776944
20       Haslach  47.990556   7.820278
21   St. Georgen  47.981111   7.804167
22      Opfingen  48.000000   7.716667
23       Tiengen  47.983333   7.713889
24     Munzingen  47.968611   7.699722
25    Weingarten  47.994444   7.810000
26    Rieselfeld  47.998889   7.791667
27        Vauban  47.975833   7.824722

3. create a map of freiburg and add markers



In [67]:
latitude=47.994828
longitude=7.849881

map_freiburg = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, lng, neighborhood in zip(freiburg_df['Latitude'], freiburg_df['Longitude'], freiburg_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_freiburg)
    
map_freiburg

4. defining foursquare ID and Secret for requests

In [18]:
CLIENT_ID = 'D0BLLEAVVZBDPTAHYQH3W3PEX2LDIUQNXQF0TBYAAZNGOMQ3' # your Foursquare ID
CLIENT_SECRET = 'HNPLFGJQQUUDZIBPVEK44NUGVRQ0STOZWPN4ECRNC4J0D45T' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: D0BLLEAVVZBDPTAHYQH3W3PEX2LDIUQNXQF0TBYAAZNGOMQ3
CLIENT_SECRET:HNPLFGJQQUUDZIBPVEK44NUGVRQ0STOZWPN4ECRNC4J0D45T


5. getting coordinates for our first neighbourhood

In [98]:
neighborhood_latitude = freiburg_df.loc[0, 'Latitude'] 
neighborhood_longitude = freiburg_df.loc[0, 'Longitude'] 

neighborhood_name =freiburg_df.loc[0, 'Neighborhood'] 

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Altstadt are 47.994721999999996, 7.85.


6. define limit and radius for our venue exploration and generating the url for request

In [114]:
LIMIT = 5000

radius = 2000

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=D0BLLEAVVZBDPTAHYQH3W3PEX2LDIUQNXQF0TBYAAZNGOMQ3&client_secret=HNPLFGJQQUUDZIBPVEK44NUGVRQ0STOZWPN4ECRNC4J0D45T&v=20180605&ll=47.994721999999996,7.85&radius=2000&limit=5000'

7. requesting the url

In [115]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f2a87dfa12e764cfd6ddd86'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Altstadt-Mitte',
  'headerFullLocation': 'Altstadt-Mitte, Freiburg',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 135,
  'suggestedBounds': {'ne': {'lat': 48.01272201800001,
    'lng': 7.876847631679049},
   'sw': {'lat': 47.97672198199998, 'lng': 7.82315236832095}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b7fed78f964a520eb4430e3',
       'name': 'Münsterplatz',
       'location': {'address': 'Münsterplatz',
        'lat': 47.9958601934988,
        'lng': 7.852422594068076,
        'labeledLatLngs': [{'label': 'display',
          'lat': 47.9

8. function that extracts the category of the venue

In [116]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

9. generating the output of our results

In [117]:

venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues


name  \
0                                        Münsterplatz   
1               Alte Wache (Haus der Badischen Weine)   
2                              Kolben Kaffee Akademie   
3                                       Burger Chalet   
4                                          Martinstor   
5                         Münster Unserer Lieben Frau   
6                              Hausbrauerei Feierling   
7                                             Euphrat   
8                                           Schlappen   
9                               Historisches Kaufhaus   
10                           Platz der Alten Synagoge   
11                                        Schwabentor   
12                                   Theater Freiburg   
13                                    Kastaniengarten   
14                                 O'Kellys Irish Pub   
15                                             Jaipur   
16                                           Basho-An   
17                               Oberkirch Weinstuben   
18                                  The Hummus Corner   
19                                           Läderach   
20                              Restaurant Wolfshöhle   
21                                         Lichtblick   
22                                Breuninger Freiburg   
23                               Feierling Biergarten   
24                                       Rathausplatz   
25                           Hotel Motel One Freiburg   
26                                          Salädchen   
27                                    Augustinerplatz   
28                                        Schlossberg   
29                                             Müller   
30                                Markthalle Freiburg   
31                                        Stadtgarten   
32                                      Casa Española   
33                                          Portofino   
34                                       Café Auszeit   
35                                        PRIMOmarket   
36                                       Martins Bräu   
37                                             Oishii   
38                                         Sedan Café   
39                            Zum Storchen La Cicogna   
40                                 Stefans Käsekuchen   
41                                            UC Café   
42                                      Colombi Hotel   
43                                             Thalia   
44                                            La Pepa   
45                                            Gmeiner   
46                   Greiffenegg Schlössle Restaurant   
47                                          Cafe Pow!   
48                Best Western Premier Hotel Victoria   
49                                Ristorante Casanova   
50                                              SKAJO   
51                                          Drexler's   
52                                           YepaYepa   
53                                    Schwarzer Kater   
54                                           Jazzhaus   
55                                         Scherazade   
56                                            Hermann   
57                                        Sofra Döner   
58                                         Oberlinden   
59                                       Kanonenplatz   
60                               Konzerthaus Freiburg   
61                               Manna - Die Spezerei   
62                               Hotel am Stadtgarten   
63                                  Weber's Weinstube   
64                                      Cafe Einstein   
65                                    Schlossbergturm   
66                                            Irodion   
67                                         Brennessel   
68                                       EDEKA Sehrer   
69                                        Café Marcel   
70

10. function to explore all neighbourhoods of freiburg

In [118]:
def getNearbyVenues(names, latitudes, longitudes, radius=3000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

11. run above function on each neighbourhood

In [119]:

freiburg_venues = getNearbyVenues(names=freiburg_df['Neighborhood'],
                                   latitudes=freiburg_df['Latitude'],
                                   longitudes=freiburg_df['Longitude']
                                  )

Altstadt
Neuburg
Herdern
Zähringen
Brühl
Hochdorf
Waldsee
Littenweiler
Ebnet
Kappel
Oberau
Wiehre
Günterstal
Stühlinger
Mooswald
Betzenhausen
Landwasser
Lehen
Waltershofen
Mundenhof
Haslach
St. Georgen
Opfingen
Tiengen
Munzingen
Weingarten
Rieselfeld
Vauban


12. size check of resulting dataframe

In [120]:
print(freiburg_venues.shape)

pd.set_option("display.max_rows", None, "display.max_columns", None)

freiburg_venues

(1576, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Altstadt              47.994722                7.850000   
1         Altstadt              47.994722                7.850000   
2         Altstadt              47.994722                7.850000   
3         Altstadt              47.994722                7.850000   
4         Altstadt              47.994722                7.850000   
5         Altstadt              47.994722                7.850000   
6         Altstadt              47.994722                7.850000   
7         Altstadt              47.994722                7.850000   
8         Altstadt              47.994722                7.850000   
9         Altstadt              47.994722                7.850000   
10        Altstadt              47.994722                7.850000   
11        Altstadt              47.994722                7.850000   
12        Altstadt              47.994722                7.850000   
13        Altstadt              47.994722                7.850000   
14        Altstadt              47.994722                7.850000   
15        Altstadt              47.994722                7.850000   
16        Altstadt              47.994722                7.850000   
17        Altstadt              47.994722                7.850000   
18        Altstadt              47.994722                7.850000   
19        Altstadt              47.994722                7.850000   
20        Altstadt              47.994722                7.850000   
21        Altstadt              47.994722                7.850000   
22        Altstadt              47.994722                7.850000   
23        Altstadt              47.994722                7.850000   
24        Altstadt              47.994722                7.850000   
25        Altstadt              47.994722                7.850000   
26        Altstadt              47.994722                7.850000   
27        Altstadt              47.994722                7.850000   
28        Altstadt              47.994722                7.850000   
29        Altstadt              47.994722                7.850000   
30        Altstadt              47.994722                7.850000   
31        Altstadt              47.994722                7.850000   
32        Altstadt              47.994722                7.850000   
33        Altstadt              47.994722                7.850000   
34        Altstadt              47.994722                7.850000   
35        Altstadt              47.994722                7.850000   
36        Altstadt              47.994722                7.850000   
37        Altstadt              47.994722                7.850000   
38        Altstadt              47.994722                7.850000   
39        Altstadt              47.994722                7.850000   
40        Altstadt              47.994722                7.850000   
41        Altstadt              47.994722                7.850000   
42        Altstadt              47.994722                7.850000   
43        Altstadt              47.994722                7.850000   
44        Altstadt              47.994722                7.850000   
45        Altstadt              47.994722                7.850000   
46        Altstadt              47.994722                7.850000   
47        Altstadt              47.994722                7.850000   
48        Altstadt              47.994722                7.850000   
49        Altstadt              47.994722                7.850000   
50        Altstadt              47.994722                7.850000   
51        Altstadt              47.994722                7.850000   
52        Altstadt              47.994722                7.850000   
53        Altstadt              47.994722                7.850000   
54        Altstadt              47.994722                7.850000   
55        Altstadt              47.994722                7.850000   
56        Altstadt              47.994722                7.850000   
57  

13. check venues for each neighbourhood

In [121]:
freiburg_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                         
Altstadt                        100                     100    100   
Betzenhausen                    100                     100    100   
Brühl                            38                      38     38   
Ebnet                            29                      29     29   
Günterstal                       47                      47     47   
Haslach                         100                     100    100   
Herdern                         100                     100    100   
Hochdorf                          8                       8      8   
Kappel                           15                      15     15   
Landwasser                       47                      47     47   
Lehen                            52                      52     52   
Littenweiler                     34                      34     34   
Mooswald                        100                     100    100   
Mundenhof                        19                      19     19   
Munzingen                        11                      11     11   
Neuburg                         100                     100    100   
Oberau                          100                     100    100   
Opfingen                          5                       5      5   
Rieselfeld                       27                      27     27   
St. Georgen                      28                      28     28   
Stühlinger                      100                     100    100   
Tiengen                           9                       9      9   
Vauban                           99                      99     99   
Waldsee                          64                      64     64   
Waltershofen                      4                       4      4   
Weingarten                      100                     100    100   
Wiehre                          100                     100    100   
Zähringen                        40                      40     40   

              Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                   
Altstadt                 100              100             100  
Betzenhausen             100              100             100  
Brühl                     38               38              38  
Ebnet                     29               29              29  
Günterstal                47               47              47  
Haslach                  100              100             100  
Herdern                  100              100             100  
Hochdorf                   8                8               8  
Kappel                    15               15              15  
Landwasser                47               47              47  
Lehen                     52               52              52  
Littenweiler              34               34              34  
Mooswald                 100              100             100  
Mundenhof                 19               19              19  
Munzingen                 11               11              11  
Neuburg                  100              100             100  
Oberau                   100              100             100  
Opfingen                   5                5               5  
Rieselfeld                27               27              27  
St. Georgen               28               28              28  
Stühlinger               100              100             100  
Tiengen                    9                9               9  
Vauban                    99               99              99  
Waldsee                   64               64              64  
Waltershofen               4                4               4  
Weingarten               100              100             100  
Wiehre                   100              100             100  
Zähringen                 40               40            

14. check venue categories

In [122]:
print('There are {} uniques categories.'.format(len(freiburg_venues['Venue Category'].unique())))

There are 93 uniques categories.


15. getting dummy variables for the venues

In [123]:
freiburg_onehot = pd.get_dummies(freiburg_venues[['Venue Category']], prefix="", prefix_sep="")

freiburg_onehot['Neighborhood'] = freiburg_venues['Neighborhood'] 

fixed_columns = [freiburg_onehot.columns[-1]] + list(freiburg_onehot.columns[:-1])
freiburg_onehot = freiburg_onehot[fixed_columns]

freiburg_onehot

Neighborhood  Asian Restaurant  Bakery  Bar  Beer Garden  Big Box Store  \
0         Altstadt                 0       0    0            0              0   
1         Altstadt                 0       0    0            0              0   
2         Altstadt                 0       0    0            0              0   
3         Altstadt                 0       0    0            0              0   
4         Altstadt                 0       0    0            0              0   
5         Altstadt                 0       0    0            0              0   
6         Altstadt                 0       0    0            0              0   
7         Altstadt                 0       0    0            0              0   
8         Altstadt                 0       0    1            0              0   
9         Altstadt                 0       0    0            1              0   
10        Altstadt                 0       0    0            0              0   
11        Altstadt                 0       0    0            0              0   
12        Altstadt                 0       0    0            0              0   
13        Altstadt                 0       0    0            0              0   
14        Altstadt                 0       0    0            0              0   
15        Altstadt                 0       0    0            0              0   
16        Altstadt                 0       0    0            0              0   
17        Altstadt                 0       0    0            0              0   
18        Altstadt                 0       0    0            0              0   
19        Altstadt                 0       0    0            0              0   
20        Altstadt                 0       0    0            0              0   
21        Altstadt                 0       0    0            0              0   
22        Altstadt                 0       0    0            0              0   
23        Altstadt                 0       0    0            0              0   
24        Altstadt                 0       0    0            1              0   
25        Altstadt                 0       0    0            0              0   
26        Altstadt                 0       0    0            0              0   
27        Altstadt                 0       0    0            0              0   
28        Altstadt                 0       0    0            0              0   
29        Altstadt                 0       0    0            0              0   
30        Altstadt                 0       0    0            0              0   
31        Altstadt                 0       0    0            0              0   
32        Altstadt                 0       0    0            0              0   
33        Altstadt                 0       0    0            0              0   
34        Altstadt                 0       0    0            0              0   
35        Altstadt                 0       0    0            0              0   
36        Altstadt                 0       0    0            0              0   
37        Altstadt                 0       0    0            0              0   
38        Altstadt                 0       0    0            0              0   
39        Altstadt                 0       0    0            0              0   
40        Altstadt                 0       0    0            0              0   
41        Altstadt                 0       0    0            0              0   
42        Altstadt                 0       0    0            0              0   
43        Altstadt                 0       0    0            0              0   
44        Altstadt                 0       0    0            0              0   
45        Altstadt                 0       0    0            0              0   
46        Altstadt                 0       0    0            0              0   
47        Altstadt                 0       0    0            0              0   
48        Altstadt                 0 

16. group dataframe

In [124]:
freiburg_grouped = freiburg_onehot.groupby('Neighborhood').mean().reset_index()
freiburg_grouped

Neighborhood  Asian Restaurant    Bakery       Bar  Beer Garden  \
0       Altstadt          0.010000  0.000000  0.030000     0.020000   
1   Betzenhausen          0.010000  0.020000  0.030000     0.000000   
2          Brühl          0.000000  0.026316  0.000000     0.000000   
3          Ebnet          0.000000  0.068966  0.000000     0.000000   
4     Günterstal          0.000000  0.063830  0.021277     0.000000   
5        Haslach          0.010000  0.010000  0.020000     0.020000   
6        Herdern          0.010000  0.000000  0.020000     0.020000   
7       Hochdorf          0.000000  0.000000  0.000000     0.000000   
8         Kappel          0.000000  0.133333  0.000000     0.000000   
9     Landwasser          0.000000  0.021277  0.021277     0.042553   
10         Lehen          0.019231  0.019231  0.019231     0.038462   
11  Littenweiler          0.000000  0.058824  0.029412     0.000000   
12      Mooswald          0.010000  0.010000  0.030000     0.000000   
13     Mundenhof          0.052632  0.000000  0.000000     0.105263   
14     Munzingen          0.000000  0.000000  0.000000     0.000000   
15       Neuburg          0.010000  0.000000  0.020000     0.020000   
16        Oberau          0.010000  0.000000  0.030000     0.020000   
17      Opfingen          0.000000  0.000000  0.000000     0.000000   
18    Rieselfeld          0.000000  0.037037  0.000000     0.037037   
19   St. Georgen          0.000000  0.107143  0.000000     0.000000   
20    Stühlinger          0.010000  0.010000  0.020000     0.020000   
21       Tiengen          0.000000  0.000000  0.000000     0.000000   
22        Vauban          0.010101  0.030303  0.030303     0.020202   
23       Waldsee          0.000000  0.031250  0.015625     0.031250   
24  Waltershofen          0.000000  0.000000  0.000000     0.000000   
25    Weingarten          0.010000  0.020000  0.030000     0.000000   
26        Wiehre          0.010000  0.000000  0.030000     0.020000   
27     Zähringen          0.000000  0.025000  0.000000     0.000000   

    Big Box Store  Bookstore  Bowling Alley   Brewery  Burger Joint  \
0        0.000000       0.00       0.000000  0.020000      0.010000   
1        0.010000       0.01       0.010000  0.010000      0.010000   
2        0.078947       0.00       0.026316  0.000000      0.000000   
3        0.000000       0.00       0.000000  0.000000      0.000000   
4        0.000000       0.00       0.000000  0.000000      0.000000   
5        0.000000       0.01       0.010000  0.020000      0.010000   
6        0.000000       0.00       0.000000  0.020000      0.010000   
7        0.000000       0.00       0.000000  0.000000      0.000000   
8        0.000000       0.00       0.000000  0.000000      0.000000   
9        0.000000       0.00       0.021277  0.000000      0.000000   
10       0.000000       0.00       0.019231  0.000000      0.000000   
11       0.000000       0.00       0.000000  0.000000      0.000000   
12       0.010000       0.01       0.010000  0.010000      0.010000   
13       0.000000       0.00       0.000000  0.000000      0.000000   
14       0.000000       0.00       0.000000  0.000000      0.000000   
15       0.000000       0.00       0.000000  0.020000      0.010000   
16       0.000000       0.00       0.000000  0.020000      0.010000   
17       0.000000       0.00       0.000000  0.000000      0.000000   
18       0.000000       0.00       0.037037  0.000000      0.000000   
19       0.000000       0.00       0.000000  0.000000      0.000000   
20       0.000000       0.01       0.000000  0.020000      0.010000   
21       0.000000       0.00       0.000000  0.000000      0.000000   
22       0.000000       0.00       0.000000  0.020202      0.010101   
23       0.000000       0.00       0.000000  0.031250      0.015625   
24       0.000000       0.00       0.000000  0.000000      0.000000   
25       0.000000       0.00       0.010000  0.010000      0.010000   
26       0.000000       0.0

17. top 5 most common venue per neighbourhood

In [132]:
num_top_venues = 10

for hood in freiburg_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = freiburg_grouped[freiburg_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Altstadt----
                      venue  freq
0                      Café  0.14
1                     Hotel  0.09
2         German Restaurant  0.06
3                     Plaza  0.06
4                Restaurant  0.03
5                       Bar  0.03
6        Italian Restaurant  0.03
7         Indian Restaurant  0.02
8            Ice Cream Shop  0.02
9  Mediterranean Restaurant  0.02


----Betzenhausen----
                    venue  freq
0                    Café  0.13
1                   Hotel  0.11
2             Supermarket  0.05
3              Restaurant  0.03
4      Italian Restaurant  0.03
5                     Bar  0.03
6       German Restaurant  0.03
7          Ice Cream Shop  0.03
8  Furniture / Home Store  0.03
9                   Plaza  0.03


----Brühl----
                    venue  freq
0                   Hotel  0.13
1             Supermarket  0.08
2           Big Box Store  0.08
3  Furniture / Home Store  0.08
4       German Restaurant  0.08
5    Fast Food Restaurant 

In [131]:
freiburg_grouped

Neighborhood  Asian Restaurant    Bakery       Bar  Beer Garden  \
0       Altstadt          0.010000  0.000000  0.030000     0.020000   
1   Betzenhausen          0.010000  0.020000  0.030000     0.000000   
2          Brühl          0.000000  0.026316  0.000000     0.000000   
3          Ebnet          0.000000  0.068966  0.000000     0.000000   
4     Günterstal          0.000000  0.063830  0.021277     0.000000   
5        Haslach          0.010000  0.010000  0.020000     0.020000   
6        Herdern          0.010000  0.000000  0.020000     0.020000   
7       Hochdorf          0.000000  0.000000  0.000000     0.000000   
8         Kappel          0.000000  0.133333  0.000000     0.000000   
9     Landwasser          0.000000  0.021277  0.021277     0.042553   
10         Lehen          0.019231  0.019231  0.019231     0.038462   
11  Littenweiler          0.000000  0.058824  0.029412     0.000000   
12      Mooswald          0.010000  0.010000  0.030000     0.000000   
13     Mundenhof          0.052632  0.000000  0.000000     0.105263   
14     Munzingen          0.000000  0.000000  0.000000     0.000000   
15       Neuburg          0.010000  0.000000  0.020000     0.020000   
16        Oberau          0.010000  0.000000  0.030000     0.020000   
17      Opfingen          0.000000  0.000000  0.000000     0.000000   
18    Rieselfeld          0.000000  0.037037  0.000000     0.037037   
19   St. Georgen          0.000000  0.107143  0.000000     0.000000   
20    Stühlinger          0.010000  0.010000  0.020000     0.020000   
21       Tiengen          0.000000  0.000000  0.000000     0.000000   
22        Vauban          0.010101  0.030303  0.030303     0.020202   
23       Waldsee          0.000000  0.031250  0.015625     0.031250   
24  Waltershofen          0.000000  0.000000  0.000000     0.000000   
25    Weingarten          0.010000  0.020000  0.030000     0.000000   
26        Wiehre          0.010000  0.000000  0.030000     0.020000   
27     Zähringen          0.000000  0.025000  0.000000     0.000000   

    Big Box Store  Bookstore  Bowling Alley   Brewery  Burger Joint  \
0        0.000000       0.00       0.000000  0.020000      0.010000   
1        0.010000       0.01       0.010000  0.010000      0.010000   
2        0.078947       0.00       0.026316  0.000000      0.000000   
3        0.000000       0.00       0.000000  0.000000      0.000000   
4        0.000000       0.00       0.000000  0.000000      0.000000   
5        0.000000       0.01       0.010000  0.020000      0.010000   
6        0.000000       0.00       0.000000  0.020000      0.010000   
7        0.000000       0.00       0.000000  0.000000      0.000000   
8        0.000000       0.00       0.000000  0.000000      0.000000   
9        0.000000       0.00       0.021277  0.000000      0.000000   
10       0.000000       0.00       0.019231  0.000000      0.000000   
11       0.000000       0.00       0.000000  0.000000      0.000000   
12       0.010000       0.01       0.010000  0.010000      0.010000   
13       0.000000       0.00       0.000000  0.000000      0.000000   
14       0.000000       0.00       0.000000  0.000000      0.000000   
15       0.000000       0.00       0.000000  0.020000      0.010000   
16       0.000000       0.00       0.000000  0.020000      0.010000   
17       0.000000       0.00       0.000000  0.000000      0.000000   
18       0.000000       0.00       0.037037  0.000000      0.000000   
19       0.000000       0.00       0.000000  0.000000      0.000000   
20       0.000000       0.01       0.000000  0.020000      0.010000   
21       0.000000       0.00       0.000000  0.000000      0.000000   
22       0.000000       0.00       0.000000  0.020202      0.010101   
23       0.000000       0.00       0.000000  0.031250      0.015625   
24       0.000000       0.00       0.000000  0.000000      0.000000   
25       0.000000       0.00       0.010000  0.010000      0.010000   
26       0.000000       0.0

18. sorting and put data in dataframe

In [126]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [127]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))


neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = freiburg_grouped['Neighborhood']

for ind in np.arange(freiburg_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(freiburg_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Altstadt                  Café                 Hotel   
1   Betzenhausen                  Café                 Hotel   
2          Brühl                 Hotel     German Restaurant   
3          Ebnet                 Hotel     German Restaurant   
4     Günterstal     German Restaurant           Supermarket   
5        Haslach                  Café                 Hotel   
6        Herdern                  Café                 Hotel   
7       Hochdorf          Liquor Store             Rest Area   
8         Kappel     German Restaurant                Bakery   
9     Landwasser                 Hotel           Supermarket   
10         Lehen                 Hotel           Supermarket   
11  Littenweiler                 Hotel     German Restaurant   
12      Mooswald                  Café                 Hotel   
13     Mundenhof                 Hotel           Supermarket   
14     Munzingen                 Hotel  Fast Food Restaurant   
15       Neuburg                  Café                 Hotel   
16        Oberau                  Café     German Restaurant   
17      Opfingen                 Hotel                  Lake   
18    Rieselfeld                 Hotel           Supermarket   
19   St. Georgen                 Hotel                Bakery   
20    Stühlinger                  Café                 Hotel   
21       Tiengen                 Hotel  Fast Food Restaurant   
22        Vauban                  Café     German Restaurant   
23       Waldsee                 Hotel     German Restaurant   
24  Waltershofen                 Hotel     German Restaurant   
25    Weingarten                  Café                 Hotel   
26        Wiehre                  Café     German Restaurant   
27     Zähringen                 Hotel     German Restaurant   

     3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
0                    Plaza       German Restaurant                   Bar   
1              Supermarket      Italian Restaurant                   Bar   
2   Furniture / Home Store           Big Box Store           Supermarket   
3             Tram Station                  Bakery            Campground   
4                   Bakery               Drugstore                 Hotel   
5                    Plaza       German Restaurant    Italian Restaurant   
6        German Restaurant                   Plaza            Restaurant   
7            Train Station            Intersection                   Gym   
8                     Pool             Supermarket    Italian Restaurant   
9   Furniture / Home Store                    Park                  Café   
10            Tram Station  Furniture / Home Store            Restaurant   
11            Tram Station                  Bakery            Campground   
12       German Restaurant                   Plaza    Italian Restaurant   
13             Beer Garden                    Café                   Zoo   
14             Gas Station       German Restaurant          Intersection   
15       German Restaurant                   Plaza    Italian Restaurant   
16                   Hotel                   Plaza                   Bar   
17              Restaurant             Gas Station     German Restaurant   
18    Gym / Fitness Center      Italian Restaurant                  Park   
19             Supermarket       German Restaurant    Italian Restaurant   
20                   Plaza       German Restaurant    Italian Restaurant   
21       German Restaurant              Restaurant           Coffee Shop   
22                   Hotel      Italian Restaurant                 Plaza   
23                   Plaza                    Café           Beer Garden   
24        Insurance Office                    Lake                  Farm   
25             Supermarket       German Restaurant    Italian Restaurant   
26                   Hotel                   Plaza    Italian Restaurant   
27  Furniture / Hom